In [5]:
import matplotlib.pyplot as plt
import pandas as pd
import geopandas as gpd
import numpy as np
import matplotlib.dates as mdates
from calendar import month_abbr
import math

In [25]:
combined_output_fpath_geojson_3_4 = './data/output/combined_output_20250417_132936.geojson'
combined_output_fpath_geojson = './data/output/combined_output_20250417_142217.geojson'

In [30]:
# Load the GeoJSON file using geopandas
# Replace 'your_file.geojson' with your actual file path
gdf = gpd.read_file(combined_output_fpath_geojson)

# Convert geopandas GeoDataFrame to pandas DataFrame if needed
swot_points = pd.DataFrame(gdf)

# Ensure illumination_time_tai is in datetime format
if not pd.api.types.is_datetime64_any_dtype(swot_points['illumination_time_tai']):
    swot_points['illumination_time_tai'] = pd.to_datetime(swot_points['illumination_time_tai'])

# Add month, year, and month-year columns for grouping
swot_points['month'] = swot_points['illumination_time_tai'].dt.month
swot_points['year'] = swot_points['illumination_time_tai'].dt.year
swot_points['month_year'] = swot_points['illumination_time_tai'].dt.to_period('M')

# Get unique reservoir indices
reservoir_indices = swot_points['index_right'].unique()
reservoir_indices = np.sort(reservoir_indices)
num_reservoirs = len(reservoir_indices)

# Calculate grid layout dimensions - now 5 plots per row
grid_cols = 5  # Fixed at 5 columns
grid_rows = math.ceil(num_reservoirs / grid_cols)

# Create figure with grid of subplots
fig, axes = plt.subplots(grid_rows, grid_cols, figsize=(4*grid_cols, 3*grid_rows), squeeze=False, dpi=500)

# Add main title
fig.suptitle("SWOT Points height Deviation Boxplot by month for Classes 3 & 4. Δ +/- 3m.", fontsize=16, y=0.99)

# Flatten the axes array for easier iteration
axes_flat = axes.flatten()

# Get all unique month-year combinations across the entire dataset
all_month_years = swot_points['month_year'].unique()
all_month_years = np.sort(all_month_years)

# Calculate overall mean for y-axis scaling if needed
height_column = 'height'  # Replace with your actual height column name
overall_mean = swot_points[height_column].mean()

# Month names for x-tick labels (abbreviated)
month_names = ['Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']

# Process each reservoir
for i, reservoir_idx in enumerate(reservoir_indices):
    if i >= len(axes_flat):
        break
        
    ax = axes_flat[i]
    
    # Filter data for current reservoir
    reservoir_data = swot_points[swot_points['index_right'] == reservoir_idx]
    
    # Calculate mean for this reservoir for y-axis scaling
    reservoir_mean = reservoir_data[height_column].mean()
    
    # Group data by month-year
    grouped_data = reservoir_data.groupby('month_year')
    
    # Prepare data for boxplot
    boxplot_data = []
    positions = []
    
    # For statistics calculation
    total_points = 0
    all_heights = []
    
    # Convert month-year periods to positions for the x-axis
    for idx, month_year in enumerate(all_month_years):
        if month_year in grouped_data.groups:
            group = grouped_data.get_group(month_year)
            # Use height values for boxplot
            heights = group[height_column]  # Replace with your actual height column
            if not heights.empty:
                boxplot_data.append(heights)
                positions.append(idx + 1)  # +1 to start at position 1
                
                # Collect data for statistics
                total_points += len(heights)
                all_heights.extend(heights.tolist())
    
    # Create monthly boxplots if data exists
    if boxplot_data:
        bp = ax.boxplot(boxplot_data, positions=positions, widths=0.7, patch_artist=True)
        
        # Style the boxplots
        for patch in bp['boxes']:
            patch.set_facecolor('lightblue')
        
        for median in bp['medians']:
            median.set(color='red', linewidth=1.5)
        
        # Calculate statistics for this reservoir
        mean_height = np.mean(all_heights)
        std_height = np.std(all_heights)
        
        # Set y-axis limits to mean +/- 3m
        ax.set_ylim(reservoir_mean - 3, reservoir_mean + 3)
        
        # Add statistics text
        stats_text = f"n={total_points}\nμ={mean_height:.2f}\nσ={std_height:.2f}"
        ax.text(0.05, 0.95, stats_text, transform=ax.transAxes, 
                verticalalignment='top', horizontalalignment='left',
                bbox=dict(boxstyle='round', facecolor='white', alpha=0.8))
    
    # Set title for each subplot
    ax.set_title(f'Reservoir {reservoir_idx}', fontsize=10)
    ax.set_xlim(0.5, len(all_month_years) + 0.5)
    
    # Set month ticks and labels for EVERY subplot
    # First, identify all month positions
    month_positions = []
    month_labels = []
    
    for idx, month_year in enumerate(all_month_years):
        month = month_year.month
        month_positions.append(idx + 1)
        month_labels.append(month_names[month-1])
    
    ax.set_xticks(month_positions)
    ax.set_xticklabels(month_labels, rotation=90, fontsize=6)
    
    # Add year labels for EVERY subplot
    # Identify positions for year labels (first month of each year)
    year_positions = []
    year_labels = []
    
    current_year = None
    for idx, month_year in enumerate(all_month_years):
        year = month_year.year
        month = month_year.month
        
        if year != current_year and month == 1:  # January of each year
            current_year = year
            year_positions.append(idx + 1)
            year_labels.append(str(year))
    
    # Create a second x-axis for year labels
    ax2 = ax.twiny()
    ax2.set_xlim(ax.get_xlim())
    ax2.set_xticks(year_positions)
    ax2.set_xticklabels(year_labels, fontsize=8)
    ax2.spines['bottom'].set_position(('axes', 25))  # Move the top spine outward
    
    # Add grid lines for better readability
    ax.grid(True, axis='y', linestyle='--', alpha=0.7)

# Hide unused subplots
for j in range(num_reservoirs, len(axes_flat)):
    axes_flat[j].axis('off')

# Add a common y-label
# fig.text(0.04, 0.5, 'Lake Height (m)', va='center', rotation='vertical', fontsize=12)

# Add a common x-label
# fig.text(0.5, 0.02, 'Months', ha='center', fontsize=12)

plt.tight_layout()
plt.subplots_adjust(top=0.92, hspace=0.6, wspace=0.3)

# Show the figure
plt.show()

# Optional: Save the figure
# plt.savefig('swot_monthly_height_distribution_by_reservoir.png', dpi=300, bbox_inches='tight')

Skipping field wavelength: unsupported OGR type: 3


In [36]:
# Load the GeoJSON file using geopandas
# Replace 'your_file.geojson' with your actual file path
gdf = gpd.read_file(combined_output_fpath_geojson_3_4)

# Convert geopandas GeoDataFrame to pandas DataFrame if needed
swot_points = pd.DataFrame(gdf)

# Ensure illumination_time_tai is in datetime format
if not pd.api.types.is_datetime64_any_dtype(swot_points['illumination_time_tai']):
    swot_points['illumination_time_tai'] = pd.to_datetime(swot_points['illumination_time_tai'])

# Add month, year, and month-year columns for grouping
swot_points['month'] = swot_points['illumination_time_tai'].dt.month
swot_points['year'] = swot_points['illumination_time_tai'].dt.year
swot_points['month_year'] = swot_points['illumination_time_tai'].dt.to_period('M')

# Get unique reservoir indices
reservoir_indices = swot_points['index_right'].unique()
reservoir_indices = np.sort(reservoir_indices)
num_reservoirs = len(reservoir_indices)

# Calculate grid layout dimensions - now 5 plots per row
grid_cols = 5  # Fixed at 5 columns
grid_rows = math.ceil(num_reservoirs / grid_cols)

# Create figure with grid of subplots
fig, axes = plt.subplots(grid_rows, grid_cols, figsize=(4*grid_cols, 3*grid_rows), squeeze=False, dpi=500)

# Add main title
fig.suptitle("SWOT Points height Deviation Boxplot by month for Classes 3 & 4. Δ +/- 3m.", fontsize=16, y=0.99)

# Flatten the axes array for easier iteration
axes_flat = axes.flatten()

# Get all unique month-year combinations across the entire dataset
all_month_years = swot_points['month_year'].unique()
all_month_years = np.sort(all_month_years)

# Calculate overall mean for y-axis scaling if needed
height_column = 'height'  # Replace with your actual height column name
overall_mean = swot_points[height_column].mean()

# Month names for x-tick labels (abbreviated)
month_names = ['Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']

# Define class_colors mapping classification types to colors
class_colors = {
    '3': 'lightblue',  # Class 3
    '4': 'lightgreen'  # Class 4
}

# Plot data by classification type and date
for i, reservoir_idx in enumerate(reservoir_indices):
    if i >= len(axes_flat):
        break
        
    ax = axes_flat[i]
    
    # Filter data for current reservoir
    reservoir_data = swot_points[swot_points['index_right'] == reservoir_idx]
    
    # Check if we have data for this reservoir
    if reservoir_data.empty:
        ax.text(0.5, 0.5, 'No data available', 
                transform=ax.transAxes, ha='center', va='center')
        continue
    
    # Calculate mean for this reservoir for y-axis scaling
    reservoir_mean = reservoir_data[height_column].mean()
    
    # Print reservoir data summary to debug
    # print(f"Reservoir {reservoir_idx}: {len(reservoir_data)} points, height range: {reservoir_data[height_column].min():.4f} to {reservoir_data[height_column].max():.4f}")
    
    # Get unique dates for this reservoir
    unique_dates = reservoir_data['illumination_time_tai'].dt.floor('D').unique()
    unique_dates = np.sort(unique_dates)
    
    # Create a mapping of date to x-position for consistent spacing
    date_positions = {date: idx for idx, date in enumerate(unique_dates)}
    
    # Statistics tracking
    total_points = 0
    all_heights = []
    
    # Check if classification column exists
    if 'classification' not in reservoir_data.columns:
        # print(f"Warning: 'classification' column not found. Using all data without classification.")
        # If no classification column, treat all data as class '3'
        reservoir_data['classification'] = '3'
    
    # Print unique classification values
    # print(f"Classifications in reservoir {reservoir_idx}: {reservoir_data['classification'].unique()}")
    
    # Plot data by classification type and date
    for classification in reservoir_data['classification'].unique():
        # Force classification to string
        classification = str(classification)
        class_data = reservoir_data[reservoir_data['classification'].astype(str) == classification]
        
        if class_data.empty:
            print(f"No data for classification {classification}")
            continue
        
        # Group by date
        class_data = class_data.copy()  # Avoid SettingWithCopyWarning
        class_data['date'] = class_data['illumination_time_tai'].dt.floor('D')
        date_groups = class_data.groupby('date')
        
        # Prepare data for boxplot
        boxplot_data = []
        positions = []
        
        for date, group in date_groups:
            heights = group[height_column].dropna()
            if not heights.empty:
                boxplot_data.append(heights.values)  # Use .values to ensure we have a numpy array
                
                # Calculate position with offset
                if classification == '3':
                    offset = -0.25
                elif classification == '4':
                    offset = 0.25
                else:
                    offset = 0  # For any other classification value
                    
                positions.append(date_positions[date] + offset)
                
                # Track statistics
                total_points += len(heights)
                all_heights.extend(heights.tolist())
        
        # print(f"Reservoir {reservoir_idx}, Class {classification}: {len(boxplot_data)} dates with data")
        
        if boxplot_data:
            # Use a color that exists in class_colors or default to gray
            color = class_colors.get(classification, 'gray')
            
            # Create boxplot
            bp = ax.boxplot(boxplot_data, positions=positions, widths=0.4, patch_artist=True)
            
            # Style the boxplots
            for patch in bp['boxes']:
                patch.set_facecolor(color)
            
            for median in bp['medians']:
                if classification == '3':
                    median.set(color='blue', linewidth=1.5)
                elif classification == '4':
                    median.set(color='green', linewidth=1.5)
            
            # Add slight transparency
            for element in ['boxes', 'whiskers', 'fliers', 'caps']:
                for item in bp[element]:
                    item.set_alpha(0.7)
    # Set axis limits and labels
    if len(unique_dates) > 0:
        ax.set_xlim(-0.5, len(unique_dates) - 0.5)
        
        # Format x-axis with dates
        num_date_ticks = min(6, len(unique_dates))
        if num_date_ticks > 0:
            tick_indices = np.linspace(0, len(unique_dates)-1, num_date_ticks, dtype=int)
            tick_positions = [idx for idx in tick_indices]
            tick_labels = [pd.Timestamp(unique_dates[idx]).strftime('%Y-%m-%d') for idx in tick_indices]
            
            ax.set_xticks(tick_positions)
            ax.set_xticklabels(tick_labels, rotation=45, fontsize=6, ha='right')
    
    # Apply y-axis limits
    if all_heights:
        mean_height = np.mean(all_heights)
        std_height = np.std(all_heights)
        
        # Set y-axis limits to mean +/- 3m
        ax.set_ylim(reservoir_mean - 3, reservoir_mean + 3)
        
        # Add statistics text
        stats_text = f"n={total_points}\nμ={mean_height:.2f}\nσ={std_height:.2f}"
        ax.text(0.05, 0.95, stats_text, transform=ax.transAxes, 
                verticalalignment='top', horizontalalignment='left',
                bbox=dict(boxstyle='round', facecolor='white', alpha=0.2))
    else:
        ax.text(0.5, 0.5, 'No valid height measurements', 
                transform=ax.transAxes, ha='center', va='center')
    
    # Set title and add grid
    ax.set_title(f'Reservoir {reservoir_idx}', fontsize=10)
    ax.grid(True, axis='y', linestyle='--', alpha=0.7)
    ax.grid(True, axis='x', linestyle=':', alpha=0.3)

# Hide unused subplots
for j in range(num_reservoirs, len(axes_flat)):
    axes_flat[j].axis('off')

# Add a common y-label
# fig.text(0.04, 0.5, 'Lake Height (m)', va='center', rotation='vertical', fontsize=12)

# Add a common x-label
# fig.text(0.5, 0.02, 'Months', ha='center', fontsize=12)

plt.tight_layout()
plt.subplots_adjust(top=0.92, hspace=0.6, wspace=0.3)

# Show the figure
plt.show()

# Optional: Save the figure
# plt.savefig('swot_monthly_height_distribution_by_reservoir.png', dpi=300, bbox_inches='tight')

Skipping field wavelength: unsupported OGR type: 3
